In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline

import seaborn as sns
plt.style.use('ggplot')

import plotly.express as px

import plotly.offline as py
py.init_notebook_mode(connected=True)
import plotly.graph_objs as go
import plotly.tools as tls
from plotly.subplots import make_subplots
import gc
import joblib
import os
import pickle

### 1. Fetch the data

In [2]:
sales = pd.read_csv('Input/sales_train_evaluation.csv')
sales.name = 'sales'

calendar = pd.read_csv('Input/calendar.csv')
calendar.name = 'calendar'

prices = pd.read_csv('Input/sell_prices.csv')
prices.name = 'prices'

Since, the validation data is now available for the days 1914-1941, Adding zero sales for days: d_1942 - d_1969(Test)

In [3]:
# Add zero sales for the remaining days : 1942 ~ 2969
for d in range(1942,1970):
    col = 'd_' + str(d)
    sales[col] = 0
    sales[col] = sales[col].astype(np.int16)

### 2. Downcasting
In this section, I'll be downcasting the dataFrames to reduce the amount of storage used by them and also to expidite the opertions performed on them

<b>Numerical Columns</b>: Depending on your environment, pandas automatically creates int32, int64, float32 or float64 columns for numeric ones. If you know the min or max value of a column, you can use a subtype which is less memory consuming. You can also use an unsigned subtype if there is no negative value.<br>
Here are the different subtypes you can use:<br>
- int8 / uint8 : consumes 1 byte of memory, range between -128/127 or 0/255
bool : consumes 1 byte, true or false
- float16 / int16 / uint16: consumes 2 bytes of memory, range between -32768 and 32767 or 0/65535
- float32 / int32 / uint32 : consumes 4 bytes of memory, range between -2147483648 and 2147483647
- float64 / int64 / uint64: consumes 8 bytes of memory

- If one of your column has values between 1 and 10 for example, you will reduce the size of that column from 8 bytes per row to 1 byte, which is more than 85% memory saving on that column!

<b>Categorical Columns</b>: Pandas stores categorical columns as objects. One of the reason this storage is not optimal is that it creates a list of pointers to the memory address of each value of your column. For columns with low cardinality (the amount of unique values is lower than 50% of the count of these values), this can be optimized by forcing pandas to use a virtual mapping table where all unique values are mapped via an integer instead of a pointer. This is done using the category datatype.


In [4]:
# Downcast in oreder ti save memort
def downcast(df):
    cols = df.dtypes.index.tolist()
    types = df.dtypes.values.tolist()
    for i,t in enumerate(types):
        if 'int' in str(t):
            if df[cols[i]].min() > np.iinfo(np.int8).min and df[cols[i]].max() < np.iinfo(np.int8).max:
                df[cols[i]] = df[cols[i]].astype(np.int8)
                
            elif df[cols[i]].min() > np.iinfo(np.int16).min and df[cols[i]].max() < np.iinfo(np.int16).max:
                df[cols[i]] = df[cols[i]].astype(np.int16)
                
            elif df[cols[i]].min() > np.iinfo(np.int32).min and df[cols[i]].max() < np.iinfo(np.int32).max:
                df[cols[i]] = df[cols[i]].astype(np.int32)
                
            else:
                df[cols[i]] = df[cols[i]].astype(np.int64)
                
        elif 'float' in str(t):
            if df[cols[i]].min() > np.finfo(np.float16).min and df[cols[i]].max() < np.finfo(np.float16).max:
                df[cols[i]] = df[cols[i]].astype(np.float16)
            elif df[cols[i]].min() > np.finfo(np.float32).min and df[cols[i]].max() < np.finfo(np.float32).max:
                df[cols[i]] = df[cols[i]].astype(np.float32)
            else:
                df[cols[i]] = df[cols[i]].astype(np.float64)
                
        elif t== np.object:
            if cols[i] == 'date':
                df[cols[i]] = pd.to_datetime(df[cols[i]],format = '%Y-%m-%d')
            else:
                df[cols[i]] = df[cols[i]].astype('category')
    return df

In [5]:
sales_bd = np.round(sales.memory_usage().sum()/(1024*1024),1)
calendar_bd = np.round(calendar.memory_usage().sum()/(1024*1024),1)
prices_bd = np.round(prices.memory_usage().sum()/(1024*1024),1)

In [6]:
sales = downcast(sales)
prices = downcast(prices)
calendar = downcast(calendar)

In [7]:
sales_ad = np.round(sales.memory_usage().sum()/(1024*1024),1)
calendar_ad = np.round(calendar.memory_usage().sum()/(1024*1024),1)
prices_ad = np.round(prices.memory_usage().sum()/(1024*1024),1)

Below plot shows how much effect downcasting has had on the memory usage of DataFrames. Clearly, we have been able to reduce sales & prices to less than 1/4th of their actual memory usage. calendar is already a small dataframe.

In [8]:
dic = {'DataFrame' : ['sales','calendar','prices'],
      'Before downcasting' : [sales_bd,calendar_bd,prices_bd],
       'After downcsting' : [sales_ad,calendar_ad,prices_ad]
        }

memory = pd.DataFrame(dic)
memory = pd.melt(memory,id_vars = 'DataFrame',var_name = 'Status',value_name = 'Memory (MB)')
memory.sort_values('Memory (MB)', inplace = True)
fig  = px.bar(memory, x = "DataFrame" , y= 'Memory (MB)', color = 'Status' ,barmode = 'group',text = 'Memory (MB)')
fig.update_traces(texttemplate = '%{text}MB',textposition = 'outside')
fig.update_layout(template = 'seaborn',title = 'Effect of Downcasting')
fig.show()

In [9]:
sales.head()

id        item_id    dept_id   cat_id store_id  \
0  HOBBIES_1_001_CA_1_evaluation  HOBBIES_1_001  HOBBIES_1  HOBBIES     CA_1   
1  HOBBIES_1_002_CA_1_evaluation  HOBBIES_1_002  HOBBIES_1  HOBBIES     CA_1   
2  HOBBIES_1_003_CA_1_evaluation  HOBBIES_1_003  HOBBIES_1  HOBBIES     CA_1   
3  HOBBIES_1_004_CA_1_evaluation  HOBBIES_1_004  HOBBIES_1  HOBBIES     CA_1   
4  HOBBIES_1_005_CA_1_evaluation  HOBBIES_1_005  HOBBIES_1  HOBBIES     CA_1   

  state_id  d_1  d_2  d_3  d_4  ...  d_1960  d_1961  d_1962  d_1963  d_1964  \
0       CA    0    0    0    0  ...       0       0       0       0       0   
1       CA    0    0    0    0  ...       0       0       0       0       0   
2       CA    0    0    0    0  ...       0       0       0       0       0   
3       CA    0    0    0    0  ...       0       0       0       0       0   
4       CA    0    0    0    0  ...       0       0       0       0       0   

   d_1965  d_1966  d_1967  d_1968  d_1969  
0       0       0       0       0       0  
1       0       0       0       0       0  
2       0       0       0       0       0  
3       0       0       0       0       0  
4       0       0       0       0       0  

[5 rows x 1975 columns]

In [10]:
calendar.head()

date  wm_yr_wk    weekday  wday  month  year    d event_name_1  \
0 2011-01-29     11101   Saturday     1      1  2011  d_1          NaN   
1 2011-01-30     11101     Sunday     2      1  2011  d_2          NaN   
2 2011-01-31     11101     Monday     3      1  2011  d_3          NaN   
3 2011-02-01     11101    Tuesday     4      2  2011  d_4          NaN   
4 2011-02-02     11101  Wednesday     5      2  2011  d_5          NaN   

  event_type_1 event_name_2 event_type_2  snap_CA  snap_TX  snap_WI  
0          NaN          NaN          NaN        0        0        0  
1          NaN          NaN          NaN        0        0        0  
2          NaN          NaN          NaN        0        0        0  
3          NaN          NaN          NaN        1        1        0  
4          NaN          NaN          NaN        1        0        1

In [11]:
calendar.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1969 entries, 0 to 1968
Data columns (total 14 columns):
date            1969 non-null datetime64[ns]
wm_yr_wk        1969 non-null int16
weekday         1969 non-null category
wday            1969 non-null int8
month           1969 non-null int8
year            1969 non-null int16
d               1969 non-null category
event_name_1    162 non-null category
event_type_1    162 non-null category
event_name_2    5 non-null category
event_type_2    5 non-null category
snap_CA         1969 non-null int8
snap_TX         1969 non-null int8
snap_WI         1969 non-null int8
dtypes: category(6), datetime64[ns](1), int16(2), int8(5)
memory usage: 144.0 KB


In [12]:
prices.head()

store_id        item_id  wm_yr_wk  sell_price
0     CA_1  HOBBIES_1_001     11325    9.578125
1     CA_1  HOBBIES_1_001     11326    9.578125
2     CA_1  HOBBIES_1_001     11327    8.257812
3     CA_1  HOBBIES_1_001     11328    8.257812
4     CA_1  HOBBIES_1_001     11329    8.257812

### 3.Melting the data
Currently, the data is in three dataframes : sales, prices  & calendar, <br>
The sales dataframe contains daily sales data with days(d_1 - d_1969) as columns.<br>
The prices dataframe contains item's price details and<br>
calendar contains data about the days d.<br>

#### 3.1 Convert from wide to long format

In this case what the melt function is doing is that it is converting the sales dataframe which is in wide format to a long format. I have kept the id variables as id, item_id, dept_id, cat_id, store_id and state_id. They have in total 30490 unique values when compunded together. Now the total number of days for which we have the data is 1969 days. Therefore the melted dataframe will be having 30490x1969 i.e. 60034810 rows

In [13]:
df = pd.melt(sales, id_vars =[ 'id','item_id','dept_id','cat_id','store_id','state_id'],var_name = 'd',value_name = 'sold').dropna()

#### 3.2 Combine the data
Combine price data from prices dataframe and days data from calendar dataset

In [14]:
df = pd.merge(df,calendar, on = 'd', how = 'left')
df = pd.merge(df,prices, on = ['store_id', 'item_id','wm_yr_wk'],how = 'left')

#### Now I have a single and a complete dataframe with all the data required. Let's Explore

### 4. Exploratory Data Analysis

#### 4.1 The Dataset
The M5 dataset, generously made available by Walmart, involves the unit sales of various products sold in the USA, organized in the form of grouped time series. More specifically, the dataset involves the unit sales of 3,049 products, classified in 3 product categories (Hobbies, Foods, and Household) and 7 product departments, in which the above-mentioned categories are disaggregated. The products are sold across ten stores, located in three States (CA, TX, and WI).

I have drawn an interactive visualization showing the distribution of 3049 items across different aggregation levels.

In [15]:
sales.head()

id        item_id    dept_id   cat_id store_id  \
0  HOBBIES_1_001_CA_1_evaluation  HOBBIES_1_001  HOBBIES_1  HOBBIES     CA_1   
1  HOBBIES_1_002_CA_1_evaluation  HOBBIES_1_002  HOBBIES_1  HOBBIES     CA_1   
2  HOBBIES_1_003_CA_1_evaluation  HOBBIES_1_003  HOBBIES_1  HOBBIES     CA_1   
3  HOBBIES_1_004_CA_1_evaluation  HOBBIES_1_004  HOBBIES_1  HOBBIES     CA_1   
4  HOBBIES_1_005_CA_1_evaluation  HOBBIES_1_005  HOBBIES_1  HOBBIES     CA_1   

  state_id  d_1  d_2  d_3  d_4  ...  d_1960  d_1961  d_1962  d_1963  d_1964  \
0       CA    0    0    0    0  ...       0       0       0       0       0   
1       CA    0    0    0    0  ...       0       0       0       0       0   
2       CA    0    0    0    0  ...       0       0       0       0       0   
3       CA    0    0    0    0  ...       0       0       0       0       0   
4       CA    0    0    0    0  ...       0       0       0       0       0   

   d_1965  d_1966  d_1967  d_1968  d_1969  
0       0       0       0       0       0  
1       0       0       0       0       0  
2       0       0       0       0       0  
3       0       0       0       0       0  
4       0       0       0       0       0  

[5 rows x 1975 columns]

In [16]:
group = sales.groupby(['state_id','store_id','cat_id','dept_id'],as_index = False)['item_id'].count().dropna()
group

state_id store_id     cat_id      dept_id  item_id
0         CA     CA_1      FOODS      FOODS_1    216.0
1         CA     CA_1      FOODS      FOODS_2    398.0
2         CA     CA_1      FOODS      FOODS_3    823.0
10        CA     CA_1    HOBBIES    HOBBIES_1    416.0
11        CA     CA_1    HOBBIES    HOBBIES_2    149.0
..       ...      ...        ...          ...      ...
611       WI     WI_3      FOODS      FOODS_3    823.0
619       WI     WI_3    HOBBIES    HOBBIES_1    416.0
620       WI     WI_3    HOBBIES    HOBBIES_2    149.0
628       WI     WI_3  HOUSEHOLD  HOUSEHOLD_1    532.0
629       WI     WI_3  HOUSEHOLD  HOUSEHOLD_2    515.0

[70 rows x 5 columns]

In [17]:
group.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 70 entries, 0 to 629
Data columns (total 5 columns):
state_id    70 non-null category
store_id    70 non-null category
cat_id      70 non-null category
dept_id     70 non-null category
item_id     70 non-null float64
dtypes: category(4), float64(1)
memory usage: 2.3 KB


In [18]:
group['USA'] = 'United States of America' # 한 열에 전부 글자가 들어감.

In [19]:
group

state_id store_id     cat_id      dept_id  item_id  \
0         CA     CA_1      FOODS      FOODS_1    216.0   
1         CA     CA_1      FOODS      FOODS_2    398.0   
2         CA     CA_1      FOODS      FOODS_3    823.0   
10        CA     CA_1    HOBBIES    HOBBIES_1    416.0   
11        CA     CA_1    HOBBIES    HOBBIES_2    149.0   
..       ...      ...        ...          ...      ...   
611       WI     WI_3      FOODS      FOODS_3    823.0   
619       WI     WI_3    HOBBIES    HOBBIES_1    416.0   
620       WI     WI_3    HOBBIES    HOBBIES_2    149.0   
628       WI     WI_3  HOUSEHOLD  HOUSEHOLD_1    532.0   
629       WI     WI_3  HOUSEHOLD  HOUSEHOLD_2    515.0   

                          USA  
0    United States of America  
1    United States of America  
2    United States of America  
10   United States of America  
11   United States of America  
..                        ...  
611  United States of America  
619  United States of America  
620  United States of America  
628  United States of America  
629  United States of America  

[70 rows x 6 columns]

In [20]:
group.rename(columns = {'state_id':'State','store_id' : 'Store', 'cat_id' : 'Category', 'dept_id' : 'Department','item_id' : 'Count'}, inplace = True )

In [21]:
group = group.reindex(columns = ['USA', 'State', 'Store', 'Category', 'Department','Count'])

In [22]:
group.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 70 entries, 0 to 629
Data columns (total 6 columns):
USA           70 non-null object
State         70 non-null category
Store         70 non-null category
Category      70 non-null category
Department    70 non-null category
Count         70 non-null float64
dtypes: category(4), float64(1), object(1)
memory usage: 2.9+ KB


fig = px.treemap(group, path=['USA', 'State', 'Store', 'Category', 'Department'], values='Count',
                  color='Count',
                  color_continuous_scale= px.colors.sequential.Sunset,
                  title='Walmart: Distribution of items')
fig.update_layout(template='seaborn')
fig.show()

#### 4.2 Item Prices
Here I'll be studying about the item prices and their distribution. Please note the prices vary weekly. So to study the distribution of prices I have taken their average.

In [23]:
group_price_store = df.groupby(['state_id','store_id','item_id'],as_index = False)['sell_price'].mean().dropna()
fig = px.violin(group_price_store,x = 'store_id',y=  'sell_price', color = 'state_id',box = True,hover_name = 'item_id')
fig.update_xaxes(title_text = 'Store')
fig.update_yaxes(title_text = 'Selling Price($)')
fig.update_layout(template = 'seaborn',title = 'Distribution of Items prices wrt Stores',legend_title_text= 'State')
fig.show()

Below are some of the observations from the above plot:-

- The distribution of item prices is almost uniform for all the stores across Califoria, Texas and Wisconsin.
- Item <b>HOBBIES_1_361</b> priced at around 30.5 dollars is the costliest item being sold at walmarts across California.
- Item <b>HOUSEHOLD_1_060</b> priced at around 29.875 dollars is the costliest item being sold at walmarts across Texas.
- Item <b>HOBBIES_1_361</b> priced at around 30.48 dollars is the costliest item being sold at TX_1 and TX_3 in Texas. While item <b>HOBBIES_1_255</b> priced at around 30.5 dollars is the costliest at TX_2

In [24]:
group_price_cat = df.groupby(['store_id','cat_id','item_id'],as_index = False)['sell_price'].mean().dropna()
fig = px.violin(group_price_cat,x = 'store_id', color = 'cat_id',y = 'sell_price',box = True,hover_name = 'item_id')
fig.update_xaxes(title_text = 'Store')
fig.update_yaxes(title_text = 'Selling Price($)')
fig.update_layout(template = 'seaborn',title = 'Distribution of Items prices wrt Stores across Categories',
                 legend_title_text=  'Category')
fig.show()

In [25]:
group_price_cat

store_id     cat_id          item_id  sell_price
0         CA_1      FOODS      FOODS_1_001    2.169922
1         CA_1      FOODS      FOODS_1_002    8.937500
2         CA_1      FOODS      FOODS_1_003    2.976562
3         CA_1      FOODS      FOODS_1_004    1.851562
4         CA_1      FOODS      FOODS_1_005    3.333984
...        ...        ...              ...         ...
91465     WI_3  HOUSEHOLD  HOUSEHOLD_2_512    3.970703
91466     WI_3  HOUSEHOLD  HOUSEHOLD_2_513    2.779297
91467     WI_3  HOUSEHOLD  HOUSEHOLD_2_514   18.796875
91468     WI_3  HOUSEHOLD  HOUSEHOLD_2_515    1.969727
91469     WI_3  HOUSEHOLD  HOUSEHOLD_2_516    5.941406

[30490 rows x 4 columns]

As can be seen from the plot above, food category items are quite cheap as compared with hobbies and household items. Hobbies and household items have almost the same price range.

#### 4.3 Items Sold
Let's Study the sales across all the stores

In [26]:
A = pd.DataFrame(np.array([1,2,3,4,5,6,7,8,9,10,11,12]).reshape(3,4),columns = ['a','b','c','d'])

In [27]:
A.groupby(['b'])['d'].sum()

b
2      4
6      8
10    12
Name: d, dtype: int32

groupby의 as_index 설명 : https://ponyozzang.tistory.com/291

In [28]:
group = df.groupby(['year','date','state_id','store_id'],as_index = False)['sold'].sum().dropna()

In [29]:
group

year       date state_id store_id    sold
0       2011 2011-01-29       CA     CA_1  4337.0
1       2011 2011-01-29       CA     CA_2  3494.0
2       2011 2011-01-29       CA     CA_3  4739.0
3       2011 2011-01-29       CA     CA_4  1625.0
14      2011 2011-01-29       TX     TX_1  2556.0
...      ...        ...      ...      ...     ...
354405  2016 2016-06-19       TX     TX_2     0.0
354406  2016 2016-06-19       TX     TX_3     0.0
354417  2016 2016-06-19       WI     WI_1     0.0
354418  2016 2016-06-19       WI     WI_2     0.0
354419  2016 2016-06-19       WI     WI_3     0.0

[19690 rows x 5 columns]

In [30]:
fig  = px.violin(group,x = 'store_id',color = 'state_id',y = 'sold',box = True)
fig.update_xaxes(title_text = 'Store')
fig.update_yaxes(title_text= 'Total items sold')
fig.update_layout(template = 'seaborn',title = 'Distribution of Items sold wrt Stores',legend_title_text = 'State')
fig.show()

Below are some of the observations from the above plot:-

- <b>California: CA_3</b> has sold the most number of items while, <b>CA_4</b> has sold the least number of items.
- <b>Texas: TX_2</b> and **TX_3** have sold the maximum number of items. <b>TX_1</b> has sold the least number of items.
- <b>Wisconsin: WI_2</b> has sold the maximum number of items while, <b>WI_3</b> has sold the least number of items.<br>
- <b>USA: CA_3</b> has sold the most number of items while, <b>CA_4</b> has sold the least number of items. <br><br>
Let's study number of items sold over time across all the stores.

In [31]:

fig = go.Figure()
title = 'Items sold over time'
years = group.year.unique().tolist()
buttons = []
y=3
for state in group.state_id.unique().tolist():
    group_state = group[group['state_id']==state]
    for store in group_state.store_id.unique().tolist():
        group_state_store = group_state[group_state['store_id']==store]
        fig.add_trace(go.Scatter(name=store, x=group_state_store['date'], y=group_state_store['sold'], showlegend=True, 
                                   yaxis='y'+str(y) if y!=1 else 'y'))
    y-=1

fig.update_layout(
        xaxis=dict(
        #autorange=True,
        range = ['2011-01-29','2016-05-22'],
        rangeselector=dict(
            buttons=list([
                dict(count=1,
                     label="1m",
                     step="month",
                     stepmode="backward"),
                dict(count=6,
                     label="6m",
                     step="month",
                     stepmode="backward"),
                dict(count=1,
                     label="YTD",
                     step="year",
                     stepmode="todate"),
                dict(count=1,
                     label="1y",
                     step="year",
                     stepmode="backward"),
                dict(count=2,
                     label="2y",
                     step="year",
                     stepmode="backward"),
                dict(count=3,
                     label="3y",
                     step="year",
                     stepmode="backward"),
                dict(count=4,
                     label="4y",
                     step="year",
                     stepmode="backward"),
                dict(step="all")
            ])
        ),
        rangeslider=dict(
            autorange=True,
        ),
        type="date"
    ),
    yaxis=dict(
        anchor="x",
        autorange=True,
        domain=[0, 0.33],
        mirror=True,
        showline=True,
        side="left",
        tickfont={"size":10},
        tickmode="auto",
        ticks="",
        title='WI',
        titlefont={"size":20},
        type="linear",
        zeroline=False
    ),
    yaxis2=dict(
        anchor="x",
        autorange=True,
        domain=[0.33, 0.66],
        mirror=True,
        showline=True,
        side="left",
        tickfont={"size":10},
        tickmode="auto",
        ticks="",
        title = 'TX',
        titlefont={"size":20},
        type="linear",
        zeroline=False
    ),
    yaxis3=dict(
        anchor="x",
        autorange=True,
        domain=[0.66, 1],
        mirror=True,
        showline=True,
        side="left",
        tickfont={"size":10},
        tickmode="auto",
        ticks='',
        title="CA",
        titlefont={"size":20},
        type="linear",
        zeroline=False
    )
    )
fig.update_layout(template='seaborn', title=title)
fig.show()

#### 4.4 State wise Analysis
In this section, I will be studying the sales and revenue of all the stores individually across all the three states: California, Texas & Wisconsin. I have plotted total three plots for each store: CA_1, CA_2, CA_3, CA_4, TX_1, TX_2, TX_3, WI_1, WI_2 & WI_3. Details about the plots are as follows:-
- First plot shows the daily sales of a store. I have plotted the values separately for SNAP days. Also, SNAP promotes food purchase, I have plotted food sales as well to check if it really affects the food sales.
- Second plot shows the daily revenue of a store with separate plotting for SNAP days.
- Third is a heatmap to show daily sales. It's plotted in such a way that it becomes easier to see day wise values.

What is SNAP?
The United States federal government provides a nutrition assistance benefit called the Supplement Nutrition Assistance Program (SNAP). SNAP provides low income families and individuals with an Electronic Benefits Transfer debit card to purchase food products. In many states, the monetary benefits are dispersed to people across 10 days of the month and on each of these days 1/10 of the people will receive the benefit on their card. More information about the SNAP program can be found [here.](https://www.fns.usda.gov/snap/supplemental-nutrition-assistance-program)

For the heatmaps, the data is till 16th week of 2016 and datetime.weekofyear of function is returning 1,2 & 3 january of 2016 in 53rd week. Plotly's heatmap is connecting the data gap between the 16th and 53rd week. Still figuring out on how to remove this gap.

In [32]:
df['revenue'] = df['sold'] * df['sell_price'].astype(np.float32)

In [33]:
def introduce_nulls(df):
    idx = pd.date_range(df.date.dt.date.min(),df.date.dt.date.max())
    df = df.set_index('date')
    df= df.reindex(idx)
    df.reset_index(inplace = True)
    df.rename(columns  = {'index':'date'},inplace = True)
    return df

def plot_metric(df,state,store,metric):
    store_sales = df[(df['state_id']==state)&(df['store_id']==store)&(df['date']<='2016-05-22')]
    food_sales = store_sales[store_sales['cat_id']=='FOODS']
    store_sales = store_sales.groupby(['date','snap_'+state],as_index=False)['sold','revenue'].sum()
    snap_sales = store_sales[store_sales['snap_'+state]==1]
    non_snap_sales = store_sales[store_sales['snap_'+state]==0]
    food_sales = food_sales.groupby(['date','snap_'+state],as_index=False)['sold','revenue'].sum()
    snap_foods = food_sales[food_sales['snap_'+state]==1]
    non_snap_foods = food_sales[food_sales['snap_'+state]==0]
    non_snap_sales = introduce_nulls(non_snap_sales)
    snap_sales = introduce_nulls(snap_sales)
    non_snap_foods = introduce_nulls(non_snap_foods)
    snap_foods = introduce_nulls(snap_foods)
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=non_snap_sales['date'],y=non_snap_sales[metric],
                           name='Total '+metric+'(Non-SNAP)'))
    fig.add_trace(go.Scatter(x=snap_sales['date'],y=snap_sales[metric],
                           name='Total '+metric+'(SNAP)'))
    fig.add_trace(go.Scatter(x=non_snap_foods['date'],y=non_snap_foods[metric],
                           name='Food '+metric+'(Non-SNAP)'))
    fig.add_trace(go.Scatter(x=snap_foods['date'],y=snap_foods[metric],
                           name='Food '+metric+'(SNAP)'))
    fig.update_yaxes(title_text='Total items sold' if metric=='sold' else 'Total revenue($)')
    fig.update_layout(template='seaborn',title=store)
    fig.update_layout(
        xaxis=dict(
        #autorange=True,
        range = ['2011-01-29','2016-05-22'],
        rangeselector=dict(
            buttons=list([
                dict(count=1,
                     label="1m",
                     step="month",
                     stepmode="backward"),
                dict(count=6,
                     label="6m",
                     step="month",
                     stepmode="backward"),
                dict(count=1,
                     label="YTD",
                     step="year",
                     stepmode="todate"),
                dict(count=1,
                     label="1y",
                     step="year",
                     stepmode="backward"),
                dict(count=2,
                     label="2y",
                     step="year",
                     stepmode="backward"),
                dict(count=3,
                     label="3y",
                     step="year",
                     stepmode="backward"),
                dict(count=4,
                     label="4y",
                     step="year",
                     stepmode="backward"),
                dict(step="all")
            ])
        ),
        rangeslider=dict(
            autorange=True,
        ),
        type="date"
    ))
    return fig

In [34]:
cal_data = group.copy()

In [35]:
cal_data.head()

year       date state_id store_id    sold
0   2011 2011-01-29       CA     CA_1  4337.0
1   2011 2011-01-29       CA     CA_2  3494.0
2   2011 2011-01-29       CA     CA_3  4739.0
3   2011 2011-01-29       CA     CA_4  1625.0
14  2011 2011-01-29       TX     TX_1  2556.0

In [36]:
cal_data = cal_data[cal_data.date <= '22-05-2016'] # date형태가 일, 월 연도 순일듯?
cal_data['week'] = cal_data.date.dt.weekofyear
cal_data['day_name'] = cal_data.date.dt.day_name()

In [37]:
cal_data.tail()

year       date state_id store_id    sold  week day_name
353565  2016 2016-05-22       TX     TX_2  5217.0    20   Sunday
353566  2016 2016-05-22       TX     TX_3  4974.0    20   Sunday
353577  2016 2016-05-22       WI     WI_1  5054.0    20   Sunday
353578  2016 2016-05-22       WI     WI_2  5068.0    20   Sunday
353579  2016 2016-05-22       WI     WI_3  4757.0    20   Sunday

In [38]:
def calmap(cal_data,state,store,scale):
    cal_data = cal_data[(cal_data['state_id'] == state) &(cal_data['store_id'] == store)]
    years = cal_data.year.unique().tolist()
    fig = make_subplots(rows = len(years),cols = 1,shared_xaxes = True,vertical_spacing = 0.005)
    r= 1
    for year in years:
        data = cal_data[cal_data['year'] == year]
        data = introduce_nulls(data)
        fig.add_trace(go.Heatmap(
            z = data.sold,
            x = data.week,
            y = data.day_name,
            hovertext = data.date.dt.date,
            coloraxis = 'coloraxis',name = year,
        ),r,1)
        fig.update_yaxes(title_text = year,tickfont = dict(size =5),row = r, col =1)
        r+=1
    fig.update_xaxes(range = [1,53],tickfont = dict(size = 10),nticks = 53)
    fig.update_layout(coloraxis = {'colorscale' : scale})
    fig.update_layout(template = 'seaborn',title =store)
    return fig

##### 캘리포니아

```
fig = plot_metric(df,'CA','CA_1','sold')
fig.show()
```

```
fig = plot_metric(df,'CA',"CA_1",'revenue')
fig.show()
```

```
fig = calmap(cal_data,'CA','CA_1','magma')
fig.show()
```

```
fig = plot_metric(df,'CA','CA_2','sold')
fig.show()
```

```
fig = plot_metric(df,'CA','CA_2','revenue')
fig.show()
```

```
fig = calmap(cal_data,'CA','CA_2','magma')
fig.show()
```

```
fig = plot_metric(df,'CA','CA_3','sold')
fig.show()
```

```
fig = plot_metric(df,'CA','CA_3','revenue')
fig.show()
```

```
fig = calmap(cal_data,'CA','CA_3','magma')
fig.show()
```

```
fig = plot_metric(df,'CA','CA_4','sold')
fig.show()
```

```
fig = plot_metric(df,'CA','CA_4','revenue')
fig.show()
```

```
fig = calmap(cal_data,'CA','CA_4','magma')
fig.show()
```

##### 텍사스

```
for i in range(3):
    print('TX_{} 그래프'.format(i+1))
    fig = plot_metric(df,'TX','TX_{}'.format(i+1),'sold')
    fig.show()
    
    fig = plot_metric(df,'TX','TX_{}'.format(i+1),'revenue')
    fig.show()
    
    fig = calmap(cal_data,'TX','TX_{}'.format(i+1),'magma')
    fig.show()
```

##### Wilcosin

```
for i in range(3):
    print('WI_{} 그래프'.format(i+1))
    fig = plot_metric(df,'WI','WI_{}'.format(i+1),'sold')
    fig.show()
    
    fig = plot_metric(df,'WI','WI_{}'.format(i+1),'revenue')
    fig.show()
    
    fig = calmap(cal_data,'WI','WI_{}'.format(i+1),'magma')
    fig.show()
    
```

In [53]:
with open('df.pickle','wb') as f:
    pickle.dump(df,f)